In [1]:
import os
os.environ['PIP_CACHE_DIR'] = '/scratch/ola5/cache'
os.environ['HF_HOME'] = '/scratch/ola5/cache'

In [2]:
%cd Open-Sora-Plan

/scratch/ola5/opensora/Open-Sora-Plan


/scratch/ola5/opensora/lib/python3.10/site-packages/IPython/core/magics/osm.py:417: UserWarning: This is now an optional IPython functionality, setting dhist requires you to install the `pickleshare` library.
  self.shell.db['dhist'] = compress_dhist(dhist)[-100:]


In [3]:
import torch

device = "cuda" if torch.cuda.is_available() else "cpu"
weight_dtype = torch.bfloat16

from diffusers.schedulers import DPMSolverMultistepScheduler
from transformers import T5EncoderModel, MT5EncoderModel, AutoTokenizer

from opensora.models.causalvideovae import ae_stride_config, ae_channel_config, ae_norm, ae_denorm, CausalVAEModelWrapper
from opensora.models.diffusion.opensora.modeling_opensora import OpenSoraT2V
#from opensora.sample.pipeline_opensora import OpenSoraPipeline
from opensora.sample.pipeline_no_encode import OpenSoraPipeline

import imageio

/scratch/ola5/opensora/lib/python3.10/site-packages/torchvision/transforms/_functional_video.py:6: UserWarning: The 'torchvision.transforms._functional_video' module is deprecated since 0.12 and will be removed in the future. Please use the 'torchvision.transforms.functional' module instead.
  warnings.warn(
/scratch/ola5/opensora/lib/python3.10/site-packages/torchvision/transforms/_transforms_video.py:22: UserWarning: The 'torchvision.transforms._transforms_video' module is deprecated since 0.12 and will be removed in the future. Please use the 'torchvision.transforms' module instead.
  warnings.warn(


[2024-08-08 02:58:28,099] [INFO] [real_accelerator.py:203:get_accelerator] Setting ds_accelerator to cuda (auto detect)
 [WARNING]  async_io requires the dev libaio .so object and headers but these were not found.
 [WARNING]  async_io: please install the libaio-dev package with apt
 [WARNING]  If libaio is already installed (perhaps from source), try setting the CFLAGS and LDFLAGS environment variables to where it can be found.
 [WARNING]  Please specify the CUTLASS repo directory as environment variable $CUTLASS_PATH


/usr/bin/ld: cannot find -laio: No such file or directory
collect2: error: ld returned 1 exit status


 [WARNING]  sparse_attn requires a torch version >= 1.5 and < 2.0 but detected 2.1
 [WARNING]  using untested triton version (2.1.0), only 1.0.0 is known to be compatible
The npu_config.on_npu is False
pid 83934's current affinity list: 0-31
pid 83934's new affinity list: 0-3


/scratch/ola5/opensora/lib/python3.10/site-packages/torchvision/transforms/functional_tensor.py:5: UserWarning: The torchvision.transforms.functional_tensor module is deprecated in 0.15 and will be **removed in 0.17**. Please don't rely on it. You probably just need to use APIs in torchvision.transforms.functional or in torchvision.transforms.v2.functional.
  warnings.warn(
/scratch/ola5/opensora/lib/python3.10/site-packages/diffusers/models/transformer_2d.py:20: FutureWarning: `Transformer2DModelOutput` is deprecated and will be removed in version 0.29. Importing `Transformer2DModelOutput` from `diffusers.models.transformer_2d` is deprecated and this will be removed in a future version. Please use `from diffusers.models.transformers.transformer_2d import Transformer2DModelOutput`, instead.
  deprecate("Transformer2DModelOutput", "0.29", deprecation_message)
/scratch/ola5/opensora/lib/python3.10/site-packages/diffusers/models/transformer_2d.py:25: FutureWarning: `Transformer2DModel` is

In [4]:
vae = CausalVAEModelWrapper("./models/vae")
vae.vae = vae.vae.to(device=device, dtype=weight_dtype)
if True:
    vae.vae.enable_tiling()
    vae.vae.tile_overlap_factor = 0.125
    vae.vae.tile_sample_min_size = 256
    vae.vae.tile_latent_min_size = 32
    vae.vae.tile_sample_min_size_t = 29
    vae.vae.tile_latent_min_size_t = 8
vae.vae_scale_factor = ae_stride_config['CausalVAEModel_D4_4x8x8']

/scratch/ola5/opensora/lib/python3.10/site-packages/diffusers/configuration_utils.py:245: FutureWarning: It is deprecated to pass a pretrained model name or path to `from_config`.If you were trying to load a model, please use <class 'opensora.models.causalvideovae.model.causal_vae.modeling_causalvae.CausalVAEModel'>.load_config(...) followed by <class 'opensora.models.causalvideovae.model.causal_vae.modeling_causalvae.CausalVAEModel'>.from_config(...) instead. Otherwise, please make sure to pass a configuration dictionary instead. This functionality will be removed in v1.0.0.
  deprecate("config-passed-as-path", "1.0.0", deprecation_message, standard_warn=False)
The config attributes {'decoder_spatial_upsample_unup': ['', '', '', ''], 'encoder_spatial_downsample_undown': ['', '', '', ''], 'in_channels': 3, 'loss_params': {'disc_start': 1, 'disc_weight': 0.5, 'kl_weight': 1e-06, 'logvar_init': 0.0}, 'loss_type': 'opensora.models.ae.videobase.losses.LPIPSWithDiscriminator', 'lr': 1e-05, 

init from ./models/vae/checkpoint.ckpt
Load from normal model!


In [5]:
transformer_model = OpenSoraT2V.from_pretrained("./models/93x720p", cache_dir='./cache_dir', low_cpu_mem_usage=False, device_map=None, torch_dtype=weight_dtype)

The config attributes {'decay': 0.999, 'inv_gamma': 1.0, 'min_decay': 0.0, 'optimization_step': 400, 'power': 0.6666666666666666, 'update_after_step': 0, 'use_ema_warmup': False} were passed to OpenSoraT2V, but are not expected and will be ignored. Please verify your config.json configuration file.


In [ ]:
text_encoder = MT5EncoderModel.from_pretrained("./models/mt5-xxl", cache_dir='./cache_dir', low_cpu_mem_usage=False, torch_dtype=weight_dtype)
tokenizer = AutoTokenizer.from_pretrained("./models/mt5-xxl", cache_dir='./cache_dir')

/scratch/ola5/opensora/lib/python3.10/site-packages/torch/_utils.py:831: UserWarning: TypedStorage is deprecated. It will be removed in the future and UntypedStorage will be the only storage class. This should only matter to you if you are using storages directly.  To access UntypedStorage directly, use tensor.untyped_storage() instead of tensor.storage()
  return self.fget.__get__(instance, owner)()


In [ ]:
transformer_model.eval()
vae.eval()
text_encoder.eval()
scheduler = DPMSolverMultistepScheduler()

In [ ]:
pipeline = OpenSoraPipeline(vae=vae, text_encoder=text_encoder, tokenizer=tokenizer, scheduler=scheduler, transformer=transformer_model)
pipeline.to(device)

In [9]:
#positive_prompt = """
#(masterpiece), (best quality), (ultra-detailed),
#{}.
#"""
#negative_prompt = """
#lowres, bad anatomy, cropped, worst quality, low quality, jpeg artifacts, signature, watermark, username, blurry
#"""

num_frames = 93
videos = pipeline(
    num_frames=num_frames,
    height=720,
    width=1280,
    num_inference_steps=20,
    guidance_scale=2.5,
    num_images_per_prompt=1,
    device=device,
    max_sequence_length=300,
).images

  0%|          | 0/20 [00:00<?, ?it/s]

OutOfMemoryError: CUDA out of memory. Tried to allocate 2.97 GiB. GPU 0 has a total capacty of 23.64 GiB of which 1.79 GiB is free. Including non-PyTorch memory, this process has 21.84 GiB memory in use. Of the allocated memory 19.18 GiB is allocated by PyTorch, and 2.20 GiB is reserved by PyTorch but unallocated. If reserved but unallocated memory is large try setting max_split_size_mb to avoid fragmentation.  See documentation for Memory Management and PYTORCH_CUDA_ALLOC_CONF

In [10]:
videos.shape

torch.Size([1, 93, 720, 1280, 3])

In [11]:
imageio.mimwrite("out1.mp4", videos[0], fps=24, quality=6)

huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)


In [12]:
from IPython.display import HTML
from base64 import b64encode

mp4 = open('/scratch/ola5/opensora/Open-Sora-Plan/out1.mp4','rb').read()
data_url = "data:video/mp4;base64," + b64encode(mp4).decode()
HTML("""
<video width=1280 controls>
      <source src="%s" type="video/mp4">
</video>
""" % data_url)

In [13]:
torch.cuda.empty_cache()